In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
cd 'drive/MyDrive/aut_sem3/embedding_pointclouds_test1/self_rag_test1'

/content/drive/MyDrive/aut_sem3/embedding_pointclouds_test1/self_rag_test1


In [ ]:
!pip install chromadb
!pip install langchain-community langchain-core
!pip install sentence-transformers
!pip install langchain_mistralai
!pip install tiktoken
!pip install huggingface_hub
!pip install "datasets>=2.6.1"

In [ ]:
from langchain.text_splitter import RecursiveCharacterTextSplitter,CharacterTextSplitter
from langchain_community.document_loaders import TextLoader
from langchain_community.vectorstores import Chroma
from langchain_community.embeddings.sentence_transformer import SentenceTransformerEmbeddings

In [ ]:
import chromadb
from chromadb.utils import embedding_functions

# Create the open-source embedding function
embedding_function1 = embedding_functions.SentenceTransformerEmbeddingFunction(model_name="all-mpnet-base-v2")

client = chromadb.PersistentClient(path="./chroma_db1")

/usr/local/lib/python3.10/dist-packages/sentence_transformers/cross_encoder/CrossEncoder.py:11: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm, trange
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavio

#1. Evaluate TriviaQA on Alpaca7b/Llama3.1:7b

In [ ]:
# col = client.get_or_create_collection(name="triviaqa-rc", embedding_function=embedding_function1)
#client.delete_collection("triviaqa_800")
#col1 = client.get_or_create_collection(name="triviaqa", embedding_function=embedding_function1)
col1 = client.get_or_create_collection(name="triviaqa_800", embedding_function=embedding_function1)

In [ ]:
from datasets import load_dataset

ds = load_dataset("mandarjoshi/trivia_qa", "rc")

Resolving data files:   0%|          | 0/26 [00:00<?, ?it/s]

Resolving data files:   0%|          | 0/26 [00:00<?, ?it/s]

Loading dataset shards:   0%|          | 0/24 [00:00<?, ?it/s]

In [ ]:
# Access the training dataset
train_dataset = ds['train']
validation_dataset = ds['validation']
test_dataset = ds['test']

# Print the first record of the training dataset
print(train_dataset[0])



{'question': 'Which American-born Sinclair won the Nobel Prize for Literature in 1930?', 'question_id': 'tc_1', 'question_source': 'http://www.triviacountry.com/', 'entity_pages': {'doc_source': [], 'filename': [], 'title': [], 'wiki_context': []}, 'search_results': {'description': ['The Nobel Prize in Literature 1930 Sinclair ... The Nobel Prize in Literature 1930 was awarded to ... nobelprize.org/nobel_prizes/literature/laureates/1930/>', 'Why Don’t More Americans Win the Nobel Prize? By . ... When the Nobel Prize in Literature was awarded to Sinclair ... In 1930, Lewis told his Nobel audience that ...', '... Sauk Centre native Sinclair Lewis became the first American to be awarded a Nobel Prize for Literature. ... in 1930, Sauk Centre native Sinclair Lewis became the ...', 'Sinclair Lewis - Nobel Prize in Literature, 1930 (20 books) Type ... Literature Fiction Classics Short Stories Essays American literature Nobel Prize Uploaded: 2015 ...', "The Nobel Prize in Literature 1930 Sincl

In [ ]:
vd=validation_dataset.select(range(200))
vd

Dataset({
    features: ['question', 'question_id', 'question_source', 'entity_pages', 'search_results', 'answer'],
    num_rows: 200
})

In [ ]:
all_answers = []

for i, record in enumerate(vd):
  all_answers.append(record['answer']['aliases'])

all_answers[4]

['Cancer pathology',
 'Deaths by cancer',
 'Anti-cancer',
 'Cancer (disease)',
 'Cancerophobia',
 'Malignant lesion',
 'Cancer medication',
 'Malignant tumors',
 'Cancer signs',
 'Malignant neoplasm',
 'Invasive (cancer)',
 'Malignant Neoplasms',
 'Malignant growth',
 'Sporadic cancer',
 'Malignant cancer',
 'Tumour virus',
 'Cancer en cuirasse',
 'Microtumor',
 'Malignant neoplasms',
 'Malignant tumour',
 'Carcinophobia',
 'Malignacy',
 'Cancer patient',
 'Epithelial cancers',
 'Solid cancer',
 'Cancers',
 'Tumor medication',
 'Malignant neoplastic disease',
 'AIDS-related cancer',
 'Invasive cancer',
 'Cancer therapy',
 'Cancerous tumor',
 'Cancer',
 'Financial toxicity',
 'Cancer diagnosis',
 'Cancer (medicine)',
 'Malignant tumor',
 'Cancerous',
 'Borderline (cancer)',
 'Signs of cancer',
 'Malignancies',
 'Cancer aromatase']

In [ ]:
unique_questions = []

for i, record in enumerate(vd):
  unique_questions.append(record['question'])

print(unique_questions[4])

What claimed the life of singer Kathleen Ferrier?


In [ ]:
#LLM
!pip install colab-xterm #https://pypi.org/project/colab-xterm/
%load_ext colabxterm

In [ ]:
%xterm
#Insert the following cmds on terminal
# `curl -fsSL https://ollama.com/install.sh | sh`
# `ollama serve & ollama pull llama3.1:latest`

Launching Xterm...

<IPython.core.display.Javascript object>

In [ ]:
# Import Ollama module from Langchain
from langchain_community.llms import Ollama

# Initialize an instance of the Ollama model
llm = Ollama(model="llama3.1:latest")

# Invoke the model to generate responses
response = llm.invoke("Who are you?", temperature=0)
print(response)

I'm an artificial intelligence model known as Llama. Llama stands for "Large Language Model Meta AI."


In [ ]:
from pydantic import BaseModel, Field
from langchain.prompts import ChatPromptTemplate

In [ ]:
def grade_documents(question, document):

  # Clean up the document by removing excessive newlines and whitespace
  cleaned_document = " ".join(document.split())

  grading_prompt = f"""
You are an expert grader tasked with determining the relevance of a retrieved document to a user question. Follow these strict instructions:

1. Carefully read the user question and the retrieved document.
2. Assess if the document contains keywords or semantic meanings related to the question.
3. Based on your assessment, determine if the document is relevant to the question.

**IMPORTANT**:
- Respond with exactly one word: 'yes' if the document is relevant, or 'no' if it is not.
- Do not provide explanations, justifications, or any other text in your response.
- PLEASE ONLY write 'yes' or 'no'.

### User question:
{question}

### Retrieved document:
{cleaned_document}

### Response:


**Please give me a 'Yes' or 'No' answer by comparing the User question and Retrieved document. I don't need any other explanation. Your output should only contain 'Yes' or 'No'. Please do the needful. Thank you.
"""

  # Assuming `llm.invoke` is the method to call the LLM
  grading_response = llm.invoke(grading_prompt, temperature=0).strip()

  # Print statements for debugging can be added here
  # print(grading_prompt)  # For debugging purposes
  # print(grading_response)  # For debugging purposes

  return grading_response


In [ ]:
def retrieve_and_grade(query):

  # Retrieve documents from ChromaDB
  retrieved_docs = col1.query(query_texts=[query], n_results=1, include=['documents'])

  # Grade each document
  graded_docs = []
  not_relevant_docs = []

  print(len(retrieved_docs['documents'][0]))

  for i in range(len(retrieved_docs['documents'][0])):
    grade = grade_documents(query, retrieved_docs['documents'][0][i])
    print(grade)  # For debugging purposes

    if grade in ['Yes', 'yes', 'yes.', 'Yes.']:
      print('Got one')
      graded_docs.append(retrieved_docs['documents'][0][i])
    elif grade in ['No', 'no', 'no.', 'No.']:
      print('Didn\'t get one')
      not_relevant_docs.append(retrieved_docs['documents'][0][i])

  return graded_docs, not_relevant_docs


In [ ]:
class CustomStrOutputParser:
    def parse(self, output):
        return output

def generate_rag_response(question, docs):
  # Flatten docs if there are nested lists
  flat_docs = []
  for doc in docs:
    if isinstance(doc, list):
      flat_docs.extend(doc)  # Flatten nested lists
    else:
      flat_docs.append(doc)

  # Ensure all elements are strings
  if not all(isinstance(doc, str) for doc in flat_docs):
    raise ValueError("All documents should be strings")

  # Clean up the document by removing excessive newlines and whitespace
  cleaned_docs = [" ".join(doc.split()) for doc in flat_docs]

  # Join documents
  formatted_docs = "\n".join(cleaned_docs)

  rag_prompt = (
      f"Based only on the following context:\n\n{formatted_docs}\n\n"
      f"Please answer the question below:\n\n{question}\n\n"
      "Only give a clean answer without any additional information. Please make sure your answer must consists of less than 4 words "
      "If you can't find the answer from the context, simply say 'I can't find the answer'."
  )

  #print(rag_prompt)

  response = llm.invoke(rag_prompt, temperature=0)

  return CustomStrOutputParser().parse(response)


In [ ]:
import string

def clean_text(text):
  # Remove punctuation from the text
  return text.translate(str.maketrans('', '', string.punctuation))

def compare_answers(rag_response, db_answer, db_question):

  # Define the revised prompt for the LLM
  prompt = f"""
  You are given a question, a RAG-generated response, and a list of ground truth answers. Your task is to determine if the RAG-generated response matches any of the ground truth answers based on the question.

  ##Question
  {db_question}

  ##Ground Truth Answer(s):
  {db_answer}

  ##RAG Response:
  {rag_response}

  Consider the RAG Response and compare it with the list of ground truth answers. A match is considered when the RAG Response closely aligns with any of the ground truth answers in terms of content and context.

  If the RAG Response closely aligns with any of the Ground Truth Answers, respond with exactly: 'Match found'
  If the RAG Response does not align closely with any of the Ground Truth Answers, respond with exactly: 'No match found'

  Please respond with only 'Match found' or 'No match found', and do not include any additional explanations.
  """

  # Invoke the model to get the comparison result
  result = llm.invoke(prompt, temperature=0)
  # Print the prompt for debugging
  print('Does the generated RAG answer match the ground truth:', result.strip())

  return result.strip()


def process_all_questions():
  # Counters for correct and incorrect answers
  correct_count = 0
  incorrect_count = 0
  missed = 0

  for i in range(0, 100):
    question = unique_questions[i]
    print('DB question:', question)

    db_answers = all_answers[i]
    print('DB answers:', db_answers)

    # Retrieve and grade documents
    graded_docs, _ = retrieve_and_grade(question)
    rag_response = generate_rag_response(question, graded_docs).strip()  # Strip whitespace
    print('Graded docs:', graded_docs)

    if graded_docs and rag_response != "I can't find the answer.":
      # Generate RAG response
      print(f"Question: {question}")
      print('RAG Response:', rag_response)

      # Compare the RAG response to the ChromaDB answers
      comparison_result = compare_answers(rag_response, db_answers, question)
      if comparison_result in ["Match found"]:
          print("Match found with DB answers.")
          correct_count += 1
      else:
          print("No match with DB answers.")
          incorrect_count += 1

      print('')
      print('')

    else:
      print(f"Question: {question}")
      print('No graded documents found or Can’t generate an answer using graded docs')
      missed += 1
      print('')
      print('')

    print('Correct Count:', correct_count)
    print('Incorrect Count:', incorrect_count)
    print('Missed question Count:', missed)

  # Calculate the ratio of correct to incorrect answers
  total_questions = correct_count + incorrect_count + missed
  if total_questions > 0:
    correct_ratio = correct_count / total_questions
    incorrect_ratio = incorrect_count / total_questions
  else:
    correct_ratio = incorrect_ratio = 0

  print(f"Total questions: {total_questions}")
  print(f"Correct answers: {correct_count}")
  print(f"Incorrect answers: {incorrect_count}")
  print(f"Correct answer ratio: {correct_ratio:.2f}")
  print(f"Incorrect answer ratio: {incorrect_ratio:.2f}")

  print('')
  print('')
  print('')

# Run the main process
process_all_questions()


DB question: Who was the man behind The Chipmunks?
DB answers: ['David Seville']
1
Yes
Got one
Graded docs: ['Alvin and the Chipmunks (2007) - IMDb\nIMDb\n17 January 2017 4:34 PM, UTC\nNEWS\nThere was an error trying to load your rating for this title.\nSome parts of this page won\'t work property. Please reload or try later.\nX Beta I\'m Watching This!\nKeep track of everything you watch; tell your friends.\nError\nAlvin and the Chipmunks\xa0( 2007 )\nPG |\nA struggling songwriter named Dave Seville finds success when he comes across a trio of singing chipmunks: mischievous leader Alvin, brainy Simon, and chubby, impressionable Theodore.\nDirector:\nFrom $2.99 (SD) on Amazon Video\nON\xa0TV\nUser Lists\nRelated lists from IMDb users\na list of 43 titles\ncreated 01\xa0Apr\xa02012\na list of 38 titles\ncreated 09\xa0May\xa02012\na list of 48 titles\ncreated 20\xa0Oct\xa02012\na list of 23 titles\ncreated 06\xa0Mar\xa02013\na list of 42 titles\ncreated 30\xa0Dec\xa02015\nTitle: Alvin an

#2. Evaluate ARC-C on Alpaca7b/Llama3.1:7b

In [ ]:
import chromadb
from chromadb.utils import embedding_functions

# Create the open-source embedding function
embedding_function1 = embedding_functions.SentenceTransformerEmbeddingFunction(model_name="all-MiniLM-L6-v2")

client = chromadb.PersistentClient(path="./chroma_db1")

In [ ]:
col1 = client.get_or_create_collection(name="arc-rag", embedding_function=embedding_function1)

In [ ]:
from datasets import load_dataset

ds = load_dataset("dpquoc/ARC-RAG")

Generating train split:   0%|          | 0/7096 [00:00<?, ? examples/s]

In [ ]:
# Access the training dataset
train_dataset = ds['train']
# validation_dataset = ds['validation']
# test_dataset = ds['test']

# Print the first record of the training dataset
print(train_dataset[0])

{'question': 'An astronomer observes that a planet rotates faster after a meteorite impact. Which is the most likely effect of this increase in rotation?', 'context': "Astronomical nutation is a phenomenon which causes the orientation of the axis of rotation of a spinning astronomical object to vary over time. It is caused by the gravitational forces of other nearby bodies acting upon the spinning object. Although they are caused by the same effect operating over different timescales, astronomers usually make a distinction between precession, which is a steady long-term change in the axis of rotation, and nutation, which is the combined effect of similar shorter-term variations. An example of precession and nutation is the variation over time of the orientation of the axis of rotation of ---and fly apart. At the time of discovery, had the smallest known rotation period in the Solar System, completing one revolution every 42.7 seconds. It is listed on the Sentry Risk Table with a 1 in 1

In [ ]:
vd=train_dataset.select(range(200))
vd

Dataset({
    features: ['question', 'context', 'A', 'B', 'C', 'D', 'answer'],
    num_rows: 200
})

In [ ]:
answer_A=[]
answer_B=[]
answer_C=[]
answer_D=[]

for i, record in enumerate(vd):
  # Extract only the values from the record and append them as a single list
  value_a = record['A']
  value_b = record['B']
  value_c = record['C']
  value_d = record['D']
  answer_A .append(value_a)
  answer_B .append(value_b)
  answer_C .append(value_c)
  answer_D .append(value_d)



In [ ]:
statement_text1 = []

for i, record in enumerate(vd):
    # Extract only the values from the record and append them as a single list
    value = record['answer']
    statement_text1 .append(value)

print(statement_text1[1])


B


In [ ]:
statement_text2= []

for i, record in enumerate(vd):
    # Extract only the values from the record and append them as a single list
    values = record['question']
    statement_text2.append(values)

print(statement_text2[1])


A group of engineers wanted to know how different building designs would respond during an earthquake. They made several models of buildings and tested each for its ability to withstand earthquake conditions. Which will most likely result from testing different building designs?


In [ ]:
context_all=[]

for i, record in enumerate(vd):
    # Extract only the values from the record and append them as a single list
    values = record['context']
    context_all.append(values)

print(context_all[1])

are not up to code may be modified to increase their resistance. Modification and earthquake resistant design are also employed in elevated freeways and bridges. Codes are not designed to make buildings earthquake proof in the sense of them suffering zero damage. The goal of most building designs is to reduce earthquake damage to a building such that it protects the lives of occupants and thus tolerance of some limited damage is accepted and considered a necessary tradeoff. A supplement or precursor to retrofitting can be the implementation of earthquake proof furniture. Earthquake modification techniques and modern building codes are ---Earthquake engineering is an interdisciplinary branch of engineering that designs and analyzes structures, such as buildings and bridges, with earthquakes in mind. Its overall goal is to make such structures more resistant to earthquakes. An earthquake (or seismic) engineer aims to construct structures that will not be damaged in minor shaking and will

In [ ]:
from pydantic import BaseModel, Field
from langchain.prompts import ChatPromptTemplate

In [ ]:
def grade_documents(question, document):
  # Clean up the document by removing excessive newlines and whitespace
  cleaned_document = " ".join(document.split())

  grading_prompt = f"""
You are an expert grader tasked with determining the relevance of a retrieved document to a user question. Follow the instructions strictly:

1. Carefully read the user question and the retrieved document.
2. Assess if the document contains keywords or semantic meanings related to the question.
3. Based on your assessment, determine if the document is relevant to the question.

**IMPORTANT**:
- Respond with exactly one word: 'yes' if the document is relevant, or 'no' if it is not.
- Do not provide explanations, justifications, or any other text in your response.

### User question:
{question}

### Retrieved document:
{cleaned_document}

### Response:
"""

  # Assuming `llm.invoke` is the method to call the LLM
  grading_response = llm.invoke(grading_prompt, temperature=0).strip()
  #print(grading_prompt)  # For debugging purposes
  print(grading_response)  # For debugging purposes

  return grading_response

# Example usage
grade_documents("What are the benefits of AI in healthcare?", "AI has been revolutionizing healthcare by providing better diagnostic tools and personalized treatment plans.")


yes


'yes'

In [ ]:
def retrieve_and_grade(query):

  # Retrieve documents from ChromaDB
  retrieved_docs = col1.query(query_texts=[query], n_results=1, include=['documents'])

  # Grade each document
  graded_docs = []
  not_relevant_docs = []

  print(len(retrieved_docs['documents'][0]))

  for i in range(len(retrieved_docs['documents'][0])):
    print(retrieved_docs['documents'][0][i])
    if grade_documents(query, retrieved_docs['documents'][0][i]) in ['yes','Yes']:
      print('Got one')
      graded_docs.append(retrieved_docs['documents'][0][i])
    if grade_documents(query, retrieved_docs['documents'][0][i]) in ['no','No']:
      print('Didnt get one')
      not_relevant_docs.append(retrieved_docs['documents'][0][i])


  return graded_docs, not_relevant_docs


In [ ]:
class CustomStrOutputParser:
  def parse(self, output):
    return output.strip()


def generate_rag_response(context, question, A, B, C, D):

    # Ensure the context is a string and clean it up
    if not isinstance(context, str):
        # If context is a list, join it into a single string
        if isinstance(context, list):
            context = " ".join(context)
        else:
            raise ValueError("Context should be a string")
    cleaned_context = " ".join(context.split())

    # Format the prompt for the RAG model
    rag_prompt = f"""
You are an expert at answering questions based on provided context. Use the information given to choose the most appropriate answer from the options provided.

Context:
{cleaned_context}

Question:
{question}

Options:
A. {A}
B. {B}
C. {C}
D. {D}

Based on the context, choose the best answer. Please provide only the letter of the answer choice (A, B, C, or D) as your response. Do not provide any explanations, reasoning, or additional information. Your output must consist of a single letter (A, B, C, or D) only.
"""

    #print(rag_prompt)  # For debugging purposes

    # Assuming `llm.invoke` is the method to call the LLM
    response = llm.invoke(rag_prompt, temperature=0).strip()
    #print('The RAG-generated answer is', response)  # For debugging purposes

    return CustomStrOutputParser().parse(response)


In [ ]:
generate_rag_response("AI has been revolutionizing healthcare by providing better diagnostic tools and personalized treatment plans.", "What are the benefits of AI in healthcare?", answer_A[i], answer_B[i], answer_C[i], answer_D[i])

'B'

In [ ]:
class CustomStrOutputParser:
  def parse(self, output):
    return output.strip()

def process_all_questions():
  # Counters for correct and incorrect answers
  correct_count = 0
  incorrect_count = 0
  missed = 0

  for i in range(0, len(vd)):

    # Generate RAG response
    rag_response = generate_rag_response(context_all[i], statement_text2[i], answer_A[i], answer_B[i], answer_C[i], answer_D[i])
    print(f"Question: {statement_text2[i]} ")
    print('RAG Response: ', rag_response )
    print('Ground Truth:', statement_text1[i])

    # Compare the RAG response to the ChromaDB answers
    if rag_response ==statement_text1[i]:
      print("Match found with DB answers.")
      correct_count += 1
    else:
      print("No match with DB answers.")
      incorrect_count += 1

    print('')
    print('')


    print('Correct Count: ',correct_count)
    print('Incorrect Count: ',incorrect_count)
    print('Missed question Count: ',missed)

  # Calculate the ratio of correct to incorrect answers
  total_questions = correct_count + incorrect_count+ missed
  if total_questions > 0:
    correct_ratio = correct_count / total_questions
    incorrect_ratio = incorrect_count / total_questions
  else:
    correct_ratio = incorrect_ratio = 0

  print(f"Total questions: {total_questions}")
  print(f"Correct answers: {correct_count}")
  print(f"Incorrect answers: {incorrect_count}")
  print(f"Correct answer ratio: {correct_ratio:.2f}")
  print(f"Incorrect answer ratio: {incorrect_ratio:.2f}")

# # Run the main process
process_all_questions()


Question: An astronomer observes that a planet rotates faster after a meteorite impact. Which is the most likely effect of this increase in rotation? 
RAG Response:  C
Ground Truth: C
Match found with DB answers.


Correct Count:  1
Incorrect Count:  0
Missed question Count:  0
Question: A group of engineers wanted to know how different building designs would respond during an earthquake. They made several models of buildings and tested each for its ability to withstand earthquake conditions. Which will most likely result from testing different building designs? 
RAG Response:  B
Ground Truth: B
Match found with DB answers.


Correct Count:  2
Incorrect Count:  0
Missed question Count:  0
Question: The end result in the process of photosynthesis is the production of sugar and oxygen. Which step signals the beginning of photosynthesis? 
RAG Response:  C
Ground Truth: C
Match found with DB answers.


Correct Count:  3
Incorrect Count:  0
Missed question Count:  0
Question: A physicist wa

#3. Evaluate PubHealth on Alpaca7b/Llama3.1:7b

In [ ]:
from datasets import load_dataset

ds = load_dataset("bigbio/pubhealth", "pubhealth_bigbio_pairs")

Generating train split:   0%|          | 0/9804 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/1231 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/1223 [00:00<?, ? examples/s]

In [ ]:
# # # col = client.get_or_create_collection(name="triviaqa-rc", embedding_function=embedding_function1)
#client.delete_collection("pubhealth")
# # #col1 = client.get_or_create_collection(name="triviaqa", embedding_function=embedding_function1)
col1 = client.get_or_create_collection(name="pubhealth", embedding_function=embedding_function1)

In [ ]:
# Access the training dataset
train_dataset = ds['train']
validation_dataset = ds['validation']
test_dataset = ds['test']

# Print the first record of the training dataset
print(train_dataset[0])



{'id': '0', 'document_id': '15661', 'text_1': '"""The money the Clinton Foundation took from from foreign governments while Hillary Clinton was secretary of state """"is clearly illegal. … The Constitution says you can’t take this stuff."""', 'text_2': '"""Gingrich said the Clinton Foundation """"took money from from foreign governments while (Hillary Clinton) was secretary of state. It is clearly illegal. … The Constitution says you can’t take this stuff."""" A clause in the Constitution does prohibit U.S. officials such as former Secretary of State Hillary Clinton from receiving gifts, or emoluments, from foreign governments. But the gifts in this case were donations from foreign governments that went to the Clinton Foundation, not Hillary Clinton. She was not part of the foundation her husband founded while she was secretary of state. Does that violate the Constitution? Some libertarian-minded constitutional law experts say it very well could. Others are skeptical. What’s clear is t

In [ ]:
vd=train_dataset.select(range(200))
vd

Dataset({
    features: ['id', 'document_id', 'text_1', 'text_2', 'label'],
    num_rows: 200
})

In [ ]:
statement_text1 = []

for i, record in enumerate(vd):
    # Extract only the values from the record and append them as a single list
    values = record['text_1']
    statement_text1 .append(values)

print(statement_text1[1])


Annual Mammograms May Have More False-Positives


In [ ]:
statement_text2= []

for i, record in enumerate(vd):
    # Extract only the values from the record and append them as a single list
    values = record['text_2']
    statement_text2.append(values)

print(statement_text2[1])


This article reports on the results of a study of nearly 170,000 women who had screening mammograms beginning between age 40-59. The study found that over ten years of screening mammograms, over half of the women will experience a false-positive recall for additional mammography. In addition, 7%-9% of the women will have a biopsy for a suspicious lump which is not cancerous. Both of those percentages decrease if the woman is screened every other year rather than every year. Even with biennial mammography, 41% of women will experience a recall over 10 years of mammography. The study’s Principal Investigator emphasized that “in most cases, a recall doesn’t mean you have cancer.”  She hoped this knowledge would reduce the anxiety of women who are recalled. The story never explained the size of the decrease in the number of false positives between annual (61.3%) and biennial screening (41.6%). Our first two reviewers were a researcher who specializes in health decisions and a breast cancer

In [ ]:
labels= []

for i, record in enumerate(vd):
    # Extract only the values from the record and append them as a single list
    values = record['label']
    labels.append(values)

print(labels[0])


false


In [ ]:
from pydantic import BaseModel, Field
from langchain.prompts import ChatPromptTemplate

In [ ]:
def grade_documents(question, document):
  # Clean up the document by removing excessive newlines and whitespace
  cleaned_document = " ".join(document.split())

  grading_prompt = f"""
You are an expert grader tasked with determining the relevance of a retrieved document to a user question. Follow the instructions strictly:

1. Carefully read the user question and the retrieved document.
2. Assess if the document contains keywords or semantic meanings related to the question.
3. Based on your assessment, determine if the document is relevant to the question.

**IMPORTANT**:
- Respond with exactly one word: 'yes' if the document is relevant, or 'no' if it is not.
- Do not provide explanations, justifications, or any other text in your response.

### User question:
{question}

### Retrieved document:
{cleaned_document}

### Response:
"""

  # Assuming `llm.invoke` is the method to call the LLM
  grading_response = llm.invoke(grading_prompt, temperature=0).strip()
  #print(grading_prompt)  # For debugging purposes
  print(grading_response)  # For debugging purposes

  return grading_response

# Example usage
grade_documents("What are the benefits of AI in healthcare?", "AI has been revolutionizing healthcare by providing better diagnostic tools and personalized treatment plans.")


yes


'yes'

In [ ]:
grade_documents('how far is to the moon', 'cricket is nice')

no


'no'

In [ ]:
def retrieve_and_grade(query):

  # Retrieve documents from ChromaDB
  retrieved_docs = col1.query(query_texts=[query], n_results=1, include=['documents'])

  # Grade each document
  graded_docs = []
  not_relevant_docs = []

  print(len(retrieved_docs['documents'][0]))

  for i in range(len(retrieved_docs['documents'][0])):
    if grade_documents(query, retrieved_docs['documents'][0][i]) in ['YES', 'Yes', 'yes', 'Yes.']:
      print('Got one')
      graded_docs.append(retrieved_docs['documents'][0][i])
    if grade_documents(query, retrieved_docs['documents'][0][i]) in ['NO', 'No', 'no', 'No.']:
      print('Didnt got one')
      not_relevant_docs.append(retrieved_docs['documents'][0][i])


  return graded_docs, not_relevant_docs


In [ ]:
class CustomStrOutputParser:
    def parse(self, output):
        return output.strip()  # Ensure the output is stripped of any extraneous whitespace

def generate_rag_response(text_2, text_1):
    # Flatten docs if there are nested lists
    flat_docs = []
    for doc in text_2:
        if isinstance(doc, list):
            flat_docs.extend(doc)  # Flatten nested lists
        else:
            flat_docs.append(doc)

    # Ensure all elements are strings
    if not all(isinstance(doc, str) for doc in flat_docs):
        raise ValueError("All documents should be strings")

    # Clean up the document by removing excessive newlines and whitespace
    cleaned_docs = [" ".join(doc.split()) for doc in flat_docs]

    # Join documents
    formatted_docs = "\n".join(cleaned_docs)

    rag_prompt = f"""
You are an expert in verifying the validity of claims based on provided context. Your task is to determine if the claim is fully supported, partially supported, not supported, or unproven by the given context. Follow the instructions below strictly:

1. **Analyze the context carefully.**
2. **Pay special attention to details indicating both what is true and what is false.**
3. **Use logical reasoning to determine the relationship between the context and the claim.**

**IMPORTANT**:
- Respond with exactly one word: 'true', 'false', 'mixture', or 'unproven'.
- Do not provide explanations, justifications, or any other text in your response.

### Context:
{formatted_docs}

### Claim:
{text_1}

### Response:
"""



    #print(rag_prompt)  # For debugging purposes

    # Assuming `llm.invoke` is the method to call the LLM
    response = llm.invoke(rag_prompt, temperature=0)
    #print('The RAG-generated answer is', response)  # For debugging purposes

    return CustomStrOutputParser().parse(response)

# Example usage
generate_rag_response([statement_text2[10]], statement_text1[10])


'mixture'

In [ ]:
generate_rag_response([statement_text2[0]], statement_text1[0]).lower()

'false'

In [ ]:
labels[10]

'true'

In [ ]:
def process_all_questions():
  # Counters for correct and incorrect answers
  correct_count = 0
  incorrect_count = 0
  missed=0

  for i in range(0, len(vd)):
    question = statement_text1[i]

    db_answers = statement_text2[i]
    print('DB context: ', db_answers)

    # Retrieve and grade documents
    graded_docs, _ = retrieve_and_grade(question)
    rag_response = generate_rag_response(graded_docs, question).lower()
    print('Graded docs: ',graded_docs)

    if graded_docs:
      # Generate RAG response
      print(f"Claim: {question} ")
      print('RAG Response: ',rag_response )
      print('Ground Truth:',labels[i] )

      # Compare the RAG response to the ChromaDB answers
      if rag_response==labels[i]:
        print("Match found with DB answers.")
        correct_count += 1
      else:
        print("No match with DB answers.")
        incorrect_count += 1

      print('')
      print('')

    else:
      print(f"Claim: {question} ")
      print('No graded documents found or Cant generate an answer using graded docs')
      missed += 1
      print('')
      print('')

    print('Correct Count: ',correct_count)
    print('Incorrect Count: ',incorrect_count)
    print('Missed question Count: ',missed)

  # Calculate the ratio of correct to incorrect answers
  total_questions = correct_count + incorrect_count+ missed
  if total_questions > 0:
    correct_ratio = correct_count / total_questions
    incorrect_ratio = incorrect_count / total_questions
  else:
    correct_ratio = incorrect_ratio = 0

  print(f"Total Claims: {total_questions}")
  print(f"Correct answers: {correct_count}")
  print(f"Incorrect answers: {incorrect_count}")
  print(f"Correct answer ratio: {correct_ratio:.2f}")
  print(f"Incorrect answer ratio: {incorrect_ratio:.2f}")

# Run the main process
process_all_questions()


DB context:  """Gingrich said the Clinton Foundation """"took money from from foreign governments while (Hillary Clinton) was secretary of state. It is clearly illegal. … The Constitution says you can’t take this stuff."""" A clause in the Constitution does prohibit U.S. officials such as former Secretary of State Hillary Clinton from receiving gifts, or emoluments, from foreign governments. But the gifts in this case were donations from foreign governments that went to the Clinton Foundation, not Hillary Clinton. She was not part of the foundation her husband founded while she was secretary of state. Does that violate the Constitution? Some libertarian-minded constitutional law experts say it very well could. Others are skeptical. What’s clear is there is room for ambiguity, and the donations are anything but """"clearly illegal."""" The reality is this a hazy part of U.S. constitutional law. "
1
yes
Got one
yes
Graded docs:  ['"""Gingrich said the Clinton Foundation """"took money fr